# Train

In [1]:
# library
import pandas as pd
import numpy as np
import pathlib
import plotly.express as px
from sklearn.cluster import KMeans
import scipy
from scipy.io import arff
from scipy import signal
from plotly.subplots import make_subplots
import plotly.graph_objects as go
import librosa
import IPython.display
import json
from tqdm import tqdm
import statistics
import random
import os
from sklearn.model_selection import GroupKFold
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.patches import Patch
from sklearn.preprocessing import LabelBinarizer
from sklearn.preprocessing import LabelEncoder
from sklearn.svm import SVR
from sklearn.model_selection import cross_validate
from sklearn.metrics import mean_absolute_error
from sklearn.model_selection import StratifiedKFold
cmap_data = plt.cm.Paired
cmap_cv = plt.cm.coolwarm

In [2]:
def seed_everything(seed):
    random.seed(seed)
    np.random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)

RANDOM_SEED = 42
seed_everything(RANDOM_SEED)

In [3]:
df_trains = []
Xs = []
for i in range(10):
    _df_train = pd.read_csv("train_unit" + str(i + 1) + ".csv")
    _X = np.load("./train_feature_unit" + str(i + 1) + ".npy")

    df_trains.append(_df_train)
    Xs.append(_X)


In [4]:
# df_sum = df_train.groupby("speaker", as_index=False).count()[["speaker", "arousal"]].rename(columns={"arousal": "count"})
# fig = px.bar(df_sum, x='speaker', y='count', template="simple_white", title="話者ごとの発話チャンク数")
# fig.show()

In [10]:
for i in range(10):
    fig = px.box(df_trains[i].sort_values("speaker"), x='speaker', y='duration', template="simple_white", title="話者ごとの発話チャンク時間の分布", width=1000)
    fig.update_yaxes(range=[0, 10])
    fig.show()

In [6]:
# fig = px.box(df_train.sort_values("speaker"), x='speaker', y='arousal', template="simple_white", title="話者ごとのArousalの分布")
# fig.update_yaxes(range=[-1, 1])
# fig.show()

In [7]:
# fig = px.box(df_train.sort_values("speaker"), x='speaker', y='valence', template="simple_white", title="話者ごとのValenceの分布")
# fig.update_yaxes(range=[-1, 1])
# fig.show()

In [8]:
# fig = px.line(df_train[df_train["speaker"] == "dev_1"], y="arousal")
# fig.show()

## Train

In [4]:
# speakerencoding
le = LabelEncoder()

# # get label
# y_arousal = df_train.arousal.values
# y_valence = df_train.valence.values

In [10]:
# def plot_cv_indices(cv, X, y, group, ax, n_splits, lw=10):
#     """Create a sample plot for indices of a cross-validation object."""

#     # Generate the training/testing visualizations for each CV split
#     for ii, (tr, tt) in enumerate(cv.split(X=X, y=y, groups=group)):
#         # Fill in indices with the training/test groups
#         indices = np.array([np.nan] * len(X))
#         indices[tt] = 1
#         indices[tr] = 0

#         # Visualize the results
#         ax.scatter(range(len(indices)), [ii + .5] * len(indices),
#                    c=indices, marker='_', lw=lw, cmap=cmap_cv, linewidth = 15,
#                    vmin=-.2, vmax=1.2)

#     # Plot the data classes and groups at the end
# #     ax.scatter(range(len(X)), [ii + 1.5] * len(X),
# #                c=y, marker='_', lw=lw, cmap=cmap_data, linewidth = 15,)

#     ax.scatter(range(len(X)), [ii + 2.5] * len(X),
#                c=group, marker='_', lw=lw, cmap=cmap_data, linewidth = 15)
    
#     ax.legend([Patch(color=cmap_cv(.8)), Patch(color=cmap_cv(.02))],
#               ['Testing set', 'Training set'], loc=(1.02, .8))

#     # Formatting
#     # yticklabels = list(range(n_splits)) + ['class', 'group']
#     yticklabels = list(range(n_splits)) + ['', 'group']
#     ax.set(yticks=np.arange(n_splits+2) + .5, yticklabels=yticklabels,
#            xlabel='Sample index', ylabel="CV iteration",
#            ylim=[n_splits+2.2, -.2], xlim=[0, len(group)])
#     ax.set_title('{}'.format(type(cv).__name__), fontsize=15)
#     return ax

In [5]:
# Group K-fold
# fig, ax = plt.subplots(figsize=(30.0, 5.0))
skf = StratifiedKFold(n_splits=5, random_state=RANDOM_SEED, shuffle=True)
# plot_cv_indices(skf, X, speakers, speakers, ax, 5)

In [12]:
# from sklearn.model_selection import GridSearchCV
# param_grid = {'kernel': ['rbf'], 'C': [0.001, 0.01, 0.1, 1, 10, 100],  'gamma' : [0.001, 0.01, 0.1, 1, 10, 100], 'epsilon': [0.0, 0.1, 0.3]}
# grid_search = GridSearchCV(SVR(), param_grid, cv=5)
# grid_search.fit(X, y_arousal)

In [13]:
# print('Test set score: {}'.format(grid_search.score(X_test, y_test)))
# print('Best parameters: {}'.format(grid_search.best_params_))
# print('Best cross-validation: {}'.format(grid_search.best_score_))

In [8]:
# svr = SVR(kernel = "rbf",gamma = 1,C=100,epsilon = 0)
# cross_validate(svr,X,y_arousal,scoring="r2",cv=gkf, groups=speakers)

def train(X, y_arousal, y_valence, speakers):

    train_scores = []
    valid_scores = []
    oof_preds = np.zeros(len(X))

    v_train_scores = []
    v_valid_scores = []
    v_oof_preds = np.zeros(len(X))

    # arousal
    print("arousal")
    for train_idx, val_idx in skf.split(X, speakers):
        # print("arousal")
        svr = SVR(kernel = "rbf")
        X_train = X[train_idx]
        y_train = y_arousal[train_idx]
        X_valid = X[val_idx]
        y_valid = y_arousal[val_idx]   

        # fit
        svr.fit(X_train, y_train)
        
        # train
        train_pred = svr.predict(X_train)
        train_score = mean_absolute_error(y_train, train_pred)
        
        # valid
        oof_pred = svr.predict(X_valid)
        valid_score = mean_absolute_error(y_valid, oof_pred)
        
        # return
        train_scores.append(train_score)
        valid_scores.append(valid_score)
        oof_preds[val_idx] = oof_pred
        
    # valence
    print("valence")
    for train_idx, val_idx in skf.split(X, speakers):
        # print("valence")
        svr = SVR(kernel = "rbf")
        X_train = X[train_idx]
        y_train = y_valence[train_idx]
        X_valid = X[val_idx]
        y_valid = y_valence[val_idx]   

        # fit
        svr.fit(X_train, y_train)
        
        # train
        train_pred = svr.predict(X_train)
        train_score = mean_absolute_error(y_train, train_pred)
        
        # valid
        oof_pred = svr.predict(X_valid)
        valid_score = mean_absolute_error(y_valid, oof_pred)
        
        # return
        v_train_scores.append(train_score)
        v_valid_scores.append(valid_score)
        v_oof_preds[val_idx] = oof_pred

    return train_scores, valid_scores, oof_preds, v_train_scores, v_valid_scores, v_oof_preds


In [11]:
ats = []
avs = []
vts = []
vvs = []

for i in range(10):
    print(i)
    speakers = le.fit_transform(df_trains[i].speaker.values)
    train_scores, valid_scores, oof_preds, v_train_scores, v_valid_scores, v_oof_preds = train(Xs[i], df_trains[i].arousal.values, df_trains[i].valence.values, speakers)

    print("train_scores", np.mean(train_scores))
    print("valid_scores", np.mean(valid_scores))
    print("v_train_scores", np.mean(v_train_scores))
    print("v_valid_scores", np.mean(v_valid_scores))

    ats.append(train_scores)
    avs.append(valid_scores)
    vts.append(v_train_scores)
    vvs.append(v_valid_scores)


0
arousal
valence
train_scores 0.15644550324182765
valid_scores 0.15856323746439613
v_train_scores 0.09831462809352123
v_valid_scores 0.09941249975102896
1
arousal
valence
train_scores 0.15593838106629296
valid_scores 0.15763444359661155
v_train_scores 0.09817930279567713
v_valid_scores 0.099090496989053
2
arousal
valence
train_scores 0.1552230623326818
valid_scores 0.15667532448451787
v_train_scores 0.09782734775120147
v_valid_scores 0.0984723330375686
3
arousal
valence
train_scores 0.15414310572834505
valid_scores 0.1552524801642547
v_train_scores 0.09736997163140848
v_valid_scores 0.09794833421421008
4
arousal
valence
train_scores 0.15317300566581543
valid_scores 0.15403746922719458
v_train_scores 0.09684134128205558
v_valid_scores 0.09735432455844623
5
arousal
valence
train_scores 0.1519543272462823
valid_scores 0.1528651031183989
v_train_scores 0.09615210375505089
v_valid_scores 0.09667318683918047
6
arousal
valence
train_scores 0.1506036644803621
valid_scores 0.15135498341511294


array([0.1564455 , 0.15593838, 0.15522306, 0.15414311, 0.15317301,
       0.15195433, 0.15060366, 0.14922551, 0.14788427, 0.1464479 ])

In [30]:
_df = pd.concat([
pd.DataFrame.from_dict({"束ねた数": np.arange(1,11,1), "metric": "train score(Arousal)", "mae": np.mean(np.array(ats), axis=1)}),
pd.DataFrame.from_dict({"束ねた数": np.arange(1,11,1), "metric": "train score(Valence)", "mae": np.mean(np.array(vts), axis=1)}),
pd.DataFrame.from_dict({"束ねた数": np.arange(1,11,1), "metric": "valid score(Arousal)", "mae": np.mean(np.array(avs), axis=1)}),
pd.DataFrame.from_dict({"束ねた数": np.arange(1,11,1), "metric": "valid score(Valence)", "mae": np.mean(np.array(vvs), axis=1)}),
])

fig = px.line(_df, x="束ねた数", y="mae", color='metric', width=1000)
fig.show()

In [36]:
# valid
fig = go.Figure()
fig.add_trace(go.Scatter(y=oof_preds,
                    mode='lines',
                    name='pred'))
fig.add_trace(go.Scatter(y=y_arousal,
                    mode='lines',
                    name='label'))
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(y=v_oof_preds,
                    mode='lines',
                    name='pred'))
fig.add_trace(go.Scatter(y=y_valence,
                    mode='lines',
                    name='label'))
fig.show()